# From classical densities to the Wigner function

In [1]:
import matplotlib
from IPython.display import SVG

matplotlib.rcParams.update({
    "figure.figsize": (8.0, 4.0),
    "figure.dpi": 160,
    "figure.autolayout": True,
    "savefig.dpi": 160,
    "savefig.bbox": "tight",
    "lines.linewidth": 1.5,
    "font.size": 12.0,
    "text.usetex": True,
    "text.latex.preamble": r"\usepackage{amsmath} \usepackage{amssymb} \usepackage{physics}",
    "axes.xmargin": 0.0,
    "axes.ymargin": 0.05,
})

## Example: the nonlinear oscillator

We have already solved the Liouville equation for a classical nonlinear
oscillator with Hamiltonian

<span id="eq-nonlinear-oscillator-classical">$$
H = \frac{p^2}{2m} + \frac{1}{2} k x^2 + g x^4.
 \qquad(1)$$</span>

Moreover, we have also solved the Schrödinger equation using QuTiP for a
simple harmonic oscillator. We now combine these two approaches to study
the **quantum nonlinear oscillator** with Hamiltonian
<a href="#eq-nonlinear-oscillator-classical"
class="quarto-xref">Equation 1</a>, but with the **quantum operator**
$\hat x$ and $\hat p$ instead of the classical variables $x$ and $p$.

In [2]:
import numpy as np
from qutip import *

N = 120
m = 0.5 # Mass of the particle
k = 2.0 # Spring constant
G = 0.15 # Nonlinear constant
w = np.sqrt(k/m) # Angular frequency

a = destroy(N)

x = np.sqrt(m * w / 2) * (a + a.dag())
p = 1j * np.sqrt(m * w / 2) * (a.dag() - a)

H = p**2 / (2 * m) + k * x**2 / 2 + G * x**4

# Initial state: coherent state
alpha = np.sqrt(1 / (2 * m * w)) * 1 + 1j * np.sqrt(m * w / 2) * 0.1
psi_0 = coherent(N, alpha)

tlist = np.linspace(0, 2, 500)
result = sesolve(H, psi_0, tlist)
result

<Result
  Solver: sesolve
  Solver stats:
    method: 'scipy zvode adams'
    init time: 0.0001971721649169922
    preparation time: 0.00016045570373535156
    run time: 0.9834189414978027
    solver: 'Schrodinger Evolution'
  Time interval: [0.0, 2.0] (500 steps)
  Number of e_ops: 0
  States saved.
>

The Wigner function can be computed from the resulting state using
QuTiP’s `wigner` function. Let’s plot its evolution over time:

In [3]:
import matplotlib.pyplot as plt
from IPython.display import HTML
from matplotlib.animation import FuncAnimation

# Phase space grid
x_list = np.linspace(-5, 5, 120)
px_list = np.linspace(-5, 5, 120)

plt.rcParams.update({"font.size": 8})
fig, ax = plt.subplots(figsize=(4.6, 2.8))

fig.suptitle(r"Wigner function evolution of a nonlinear oscillator")

img = ax.pcolormesh(x_list, px_list, wigner(result.states[0], x_list, px_list),
                    shading="gouraud", rasterized=True,
                    vmin=-0.3, vmax=0.3, cmap="PuOr")
ax.set_xlabel("Position $x$")
ax.set_ylabel("Momentum $p_x$")

def animate(i):
  wig_i = wigner(result.states[i], x_list, px_list)
  img.set_array(wig_i.ravel())
  return img,

ani = FuncAnimation(fig, animate, frames=range(0, len(tlist), 10), interval=200, blit=True)

plt.close(fig)
HTML(ani.to_jshtml())

Once 
 
 Loop 
 
 Reflect

Or we plot the final Wigner function as a 2D plot:

In [4]:
plt.rcParams.update({"font.size": 12})

In [5]:
fig, ax = plt.subplots()

img = ax.pcolormesh(x_list, px_list, wigner(result.states[-1], x_list, px_list),
                    shading="gouraud", rasterized=True,
                    vmin=-0.3, vmax=0.3, cmap="PuOr")
ax.set_xlabel("Position $x$")
ax.set_ylabel("Momentum $p_x$")

# Show in Quarto
plt.savefig("_tmp_fig.svg")
plt.close(fig)
SVG("_tmp_fig.svg")